In [96]:
import pandas as pd 
import numpy as np
from itertools import permutations


In [97]:
IND = {"age":["59","54","35","73","49"],
      "sex":["M","M","M","F","F"]}
IND = pd.DataFrame(IND)
IND["age"] = IND["age"].apply(pd.to_numeric)
print(IND)

   age sex
0   59   M
1   54   M
2   35   M
3   73   F
4   49   F


In [106]:
Under50 = []
Over50 = []
M = []
F = []

for i in range(len(IND)):
    
    if IND.loc[i,"age"] < 50: 
            Under50.append(1)
            Over50.append(0)

    elif IND.loc[i,"age"] > 50: 
            Under50.append(0)
            Over50.append(1)

for i in range(len(IND)):

    if IND.loc[i,"sex"] == "M": 
            M.append(1)
            F.append(0)
            
    elif IND.loc[i,"sex"] == "F": 
            M.append(0)
            F.append(1)
            
        

IND_Agg =[Under50,Over50,M,F]
print(IND_Agg)

[[0, 0, 1, 0, 1], [1, 1, 0, 1, 0], [1, 1, 1, 0, 0], [0, 0, 0, 1, 1]]


In [99]:
CONS = {"Under50":["8"],"Over50": ["4"],"M" : ["6"],"F" : ["6"]}
CONS = pd.DataFrame(CONS) 
for col in CONS: 
    CONS[col] = CONS[col].apply(pd.to_numeric)


print(CONS)

   Under50  Over50  M  F
0        8       4  6  6


In [154]:
#Main IPF Algorithmn

weight = [1,1,1,1,1]

def IPF(X,Y):
    for k in range(len(Y.columns)):
        X_new = np.multiply(weight,X[k])
        for i in range(len(X[k])):
            if X[k][i] == 1:
                weight[i] = weight[i]*Y.iloc[0,k]/sum(X_new)
            else: 
                weight[i] = weight[i]
    print(weight)
    print("Iteration " + str(k))
    TAE = Y.iloc[0,k] - sum(X_new) 
    print(TAE)
    #print(X_new)
   
IPF(IND_Agg,CONS)
            
            

[1.2000000000000002, 1.2000000000000002, 3.6000000000000005, 1.5, 4.5]
Iteration 3
0.666666666666667
[0.         0.         0.         1.33333333 4.        ]


In [173]:
# Python function to print permutations of a given list 
def permutation(lst): 
  
    # If lst is empty then there are no permutations 
    if len(lst) == 0: 
        return [] 
  
    # If there is only one element in lst then, only 
    # one permuatation is possible 
    if len(lst) == 1: 
        return [lst] 
  
    # Find the permutations for lst if there are 
    # more than 1 characters 
  
    l = [] # empty list that will store current permutation 
  
    # Iterate the input(lst) and calculate the permutation 
    for i in range(len(lst)): 
       m = lst[i] 
  
       # Extract lst[i] or m from the list.  remLst is 
       # remaining list 
       remLst = lst[:i] + lst[i+1:] 
  
       # Generating all permutations where m is first 
       # element 
       for p in permutation(remLst): 
           l.append([m] + p) 
    return l 

In [172]:
permutation(IND_Agg)[0]

[[0, 0, 1, 0, 1], [1, 1, 0, 1, 0], [1, 1, 1, 0, 0], [0, 0, 0, 1, 1]]

In [ ]:
def IPF2(X,Y,max_iteration = 1):
    
    weight = [1,1,1,1,1]
    
    #Number of iteration for each permutation order 
    iteration = 0
    
    #Generate all possible permutation for individual data 
    perm = permutation(X)
    
    #Generate all possible permutation for Constraint data 
    perm2 = permutation(Y)
    
    #While statement that loop through all iteration till it achieves max_iteration
    while iteration < max_iteration: 
        
        #Generate new individual data for each iteration 
        #For example, the first iteration has the following order: M, <50, F, >50 
        X_new = perm[iteration]

        #Generate new Constraints data for each iteration 
        #For example, the first iteration has the following order: M, <50, F, >50
        Y_new = perm2[iteration]
        
        #Note: The variables order of constraint and individual should be the same
        
        #Run IPF for each iteration
        IPF(X_new,Y_new)

    #After each iteration add 1 
    iteration += 1 

IPF2(IND_Agg,CONS,max_iteration = 4 )

[1.2272727272727273, 1.2272727272727273, 3.5454545454545454, 1.542857142857143, 4.457142857142857]
Iteration 3
0.01709401709401792
[0.         0.         0.         1.53846154 4.44444444]
[1.2279792746113989, 1.2279792746113989, 3.5440414507772022, 1.5439739413680782, 4.456026058631922]
Iteration 3
0.00044414834554729055
[0.         0.         0.         1.54385965 4.4556962 ]
[1.227997637330183, 1.227997637330183, 3.544004725339634, 1.5440029706646863, 4.455997029335313]
Iteration 3
1.1544011543129784e-05
[0.         0.         0.         1.544      4.45598846]
[1.2279981146050771, 1.2279981146050771, 3.5440037707898457, 1.5440037251830845, 4.455996274816915]
Iteration 3
3.0004695084073774e-07
[0.         0.         0.         1.54400365 4.45599605]
[1.2279981270102016, 1.2279981270102016, 3.544003745979597, 1.5440037447942054, 4.455996255205795]
Iteration 3
7.798693246741095e-09
[0.         0.         0.         1.54400374 4.45599625]
[1.2279981273326304, 1.2279981273326304, 3.544003

In [ ]:
#Different order 

weight = [1,1,1,1,1]



def IPF(X,Y,max_iteration = 1):
    
    '''
    Since IPF is sensitive to the order of iteration 
    This function considers all the possible permutation of the order of the constraints 
    And find the optimal permutation for the smallest TAE  
    
    '''
    #Number of iteration for each permutation order 
    iteration = 0
    
    #Generate all possible permutation for individual data 
    perm = list(permutations(X)) 
    
    #Generate all possible permutation for Constraint data 
    perm2 = list(permutations(Y))
    
    #While statement that loop through all iteration till it achieves max_iteration
    while iteration < max_iteration:
        
        #Generate new individual data for each iteration 
        #For example, the first iteration has the following order: M, <50, F, >50 
        X_new = perm[iteration]

        #Generate new Constraints data for each iteration 
        #For example, the first iteration has the following order: M, <50, F, >50
        Y_new = perm2[iteration]
        
        #Note: The variables order of constraint and individual should be the same

        #For statement that loops through all the varaibles in the constraint dataset 
        for k in range(len(Y.columns)):
            
            #Generate new cell counts using the current weight
            X_new = np.multiply(weight,X_new[k])
            
            #For statement that loops through all the individual in the individual dataset 
            for i in range(len(X)):
                
                #IF else statement, if the 
                if X_new[i] == 1:
                    
                    weight[i] = weight[i]*Y.loc[0,Y_new[k]]/sum(X_new)
                    
                else: 
                    
                    weight[i] = weight[i]
                    
        print(weight)
        #print("Iteration " + str(k))
        #TAE = Y.iloc[0,k] - sum(X_new) 
        #print(TAE)
        iteration += 1 
   
IPF(IND_Agg,CONS,max_iteration = 4 )